# Web Scraping Data for Raw Votes by County

Votes for elections by county are now easy to come by in a comprehensive format. This notebook scrapes that data from the site townhall.com for the past four presidential elections and puts them into separates dataframes.
Votes for Alaska aren't included because they don't vote by county and their voting districts are not labeled well for comparing to economic estimators. 

In [69]:
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup
import requests
import time

In [70]:
pd.set_option("display.max_rows", 4000)

In [71]:
url = 'https://townhall.com/election/{}/president/{}/county'

In [72]:
# set list of states to interate over all counties in all states, missing alaska
states = ['al','az','ar','ca','co','ct','de','fl','ga','hi','id','il','in','ia','ks',
          'ky','la','me','md','ma','mi','mn','ms','mo','mt','ne','nv','nh','nj','nm','ny',
          'nc','nd','oh','ok','or','pa','ri','sc','sd','tn','tx','ut','vt','va','wa','wv',
          'wi','wy']

# set url of site to scrap from
url = 'https://townhall.com/election/{}/president/{}/county'

# lists of candidates for each year, to match election year entered into function
candidates_2004 = ['George Bush', 'John Kerry', 'Ralph Nader']
candidates_2008 = ['Barack Obama', 'John McCain']
candidates_2012 = ['Barack Obama', 'Mitt Romney', 'Gary Johnson', 'Other']
candidates_2016 = ['Hillary Clinton', 'Donald Trump', 'Gary Johnson', 'Jill Stein']


def data(year, candidates):
    '''Function that scrapes the site townhall.com for election data by county. Loops over 
    each state's page and outputs data for election year entered.'''
    
    # initialize empty lists
    rep_vote = []
    dem_vote = []
    counties = []
    
    # scrapes each state's page using list of states from above
    for state in states:
        res = requests.get(url .format(year, state))
        soup = BeautifulSoup(res.content, 'lxml')
        
        
        rows = soup.find_all('tbody')
        
        if len(rows) == 2:
            rows = soup.find_all('tbody')[1]
        else:
            rows = soup.find_all('tbody')

        # loops over rows to pull out county names
        for row in rows:
            count = []
            x = row.find('div')
            # filters returns from div returns three types of values (the county name, -1 and None) 
            # then appends to empty list to create list of lists, which will later be flattend
            if type(x) != int and x != None:
                county = x.text
                count.append(county)
                count = list(set(count))
                count.sort()
                count = [str(x + ', ' + state.upper()) for x in count]
                counties.append(count)

        # Republican Results - finds data from text with 'republican' class
        # finds class of REP and GOP, different for different years
        
        
        row = rows.find_all('td', {'class':  ['REP', 'GOP']})

        for x in row:
            if '.' not in x.text and x.text not in candidates:
                rep_vote.append(x.text.replace(',', ''))
                
       # Democratic Results - finds data from text with 'democratic' class

        row = rows.find_all('td', {'class': 'DEM'})
        

        for x in row:
            if '.' not in x.text and x.text not in candidates:
                dem_vote.append(x.text.replace(',', ''))
                
            
    return counties, dem_vote, rep_vote

## 2004 Election

In [97]:
count, dem_vote, rep_vote = data(2004, candidates_2004)

# check to make sure lists are the same length
print(len(count), len(dem_vote), len(rep_vote))

# loop over counties list to convert from list of lists or strings, to list of strings
counties = [item for sublist in count for item in sublist]

# empty DataFrame
results_2004 = pd.DataFrame()
        
# add lists to empty Data Frame
results_2004['county'] = counties
results_2004['dem_vote'] = dem_vote
results_2004['rep_vote'] = rep_vote
results_2004['year'] = 2004

results_2004

3110 3110 3110


county dem_vote rep_vote  year
0                  Autauga, AL     4774    15212  2004
1                  Baldwin, AL    15579    52910  2004
2                  Barbour, AL     4826     5893  2004
3                     Bibb, AL     2089     5471  2004
4                   Blount, AL     3932    17364  2004
5                  Bullock, AL     3210     1494  2004
6                   Butler, AL     3409     4978  2004
7                  Calhoun, AL    15076    29806  2004
8                 Chambers, AL     5346     7618  2004
9                 Cherokee, AL     3036     5919  2004
10                 Chilton, AL     3773    12824  2004
11                 Choctaw, AL     3289     3889  2004
12                  Clarke, AL     4627     6729  2004
13                    Clay, AL     1893     4622  2004
14                Cleburne, AL     1387     4362  2004
15                  Coffee, AL     4477    13010  2004
16                 Colbert, AL    10586    13179  2004
17                 Conecuh, AL     2715     3266  2004
18                   Coosa, AL     2055     2902  2004
19               Covington, AL     3422    11108  2004
20                Crenshaw, AL     1698     3774  2004
21                 Cullman, AL     8022    26783  2004
22                    Dale, AL     4479    13614  2004
23                  Dallas, AL    11145     7318  2004
24                  DeKalb, AL     7092    16901  2004
25                  Elmore, AL     6455    22024  2004
26                Escambia, AL     3812     8501  2004
27                  Etowah, AL    15311    26972  2004
28                 Fayette, AL     2408     5532  2004
29                Franklin, AL     4513     7688  2004
30                  Geneva, AL     2105     8324  2004
31                  Greene, AL     3763      958  2004
32                    Hale, AL     4622     3278  2004
33                   Henry, AL     2432     4859  2004
34                 Houston, AL     9141    26868  2004
35                 Jackson, AL     8618    11507  2004
36               Jefferson, AL   132145   158504  2004
37                   Lamar, AL     1956     4894  2004
38              Lauderdale, AL    14615    22123  2004
39                Lawrence, AL     6153     7728  2004
40                     Lee, AL    16177    27911  2004
41               Limestone, AL     8859    18994  2004
42                 Lowndes, AL     4233     1786  2004
43                   Macon, AL     7495     1540  2004
44                 Madison, AL    52614    77150  2004
45                 Marengo, AL     5026     5242  2004
46                  Marion, AL     3806     8983  2004
47                Marshall, AL     8441    22745  2004
48                  Mobile, AL    63614    91877  2004
49                  Monroe, AL     3666     5831  2004
50              Montgomery, AL    45127    44074  2004
51                  Morgan, AL    14113    32435  2004
52                   Perry, AL     3754     1733  2004
53                 Pickens, AL     3915     5170  2004
54                    Pike, AL     4323     7473  2004
55                Randolph, AL     2817     6127  2004
56                 Russell, AL     8372     8332  2004
57                  Shelby, AL    14826    63326  2004
58               St. Clair, AL     5449    23468  2004
59                  Sumter, AL     4527     1880  2004
60               Talladega, AL    11373    18326  2004
61              Tallapoosa, AL     5449    12378  2004
62              Tuscaloosa, AL    26420    42827  2004
63                  Walker, AL     9012    19162  2004
64              Washington, AL     3127     5042  2004
65                  Wilcox, AL     3238     1778  2004
66                 Winston, AL     2234     8052  2004
67                  Apache, AZ    15082     8068  2004
68                 Cochise, AZ    16219    24828  2004
69                Coconino, AZ    26513    20619  2004
70                    Gila, AZ     7107    10494  2004
71                  Graham, AZ     3141     7302  2004
72       

## 2008 Election

In [98]:
count, dem_vote, rep_vote = data(2008, candidates_2008)

# check to make sure lists are the same length
print(len(count), len(dem_vote), len(rep_vote))

# loop over counties list to convert from list of lists or strings, to list of strings
counties = [item for sublist in count for item in sublist]

# empty DataFrame
results_2008 = pd.DataFrame()

# add lists to empty Data Frame
results_2008['county'] = counties
results_2008['dem_vote'] = dem_vote
results_2008['rep_vote'] = rep_vote
results_2008['year'] = 2008

results_2008

3112 3112 3112


county dem_vote rep_vote  year
0                  Autauga, AL     6091    17398  2008
1                  Baldwin, AL    19362    61192  2008
2                  Barbour, AL     5685     5862  2008
3                     Bibb, AL     2289     6247  2008
4                   Blount, AL     3518    20362  2008
5                  Bullock, AL     4001     1389  2008
6                   Butler, AL     4174     5472  2008
7                  Calhoun, AL    16325    32326  2008
8                 Chambers, AL     6782     8060  2008
9                 Cherokee, AL     2299     7285  2008
10                 Chilton, AL     3666    13934  2008
11                 Choctaw, AL     3633     4220  2008
12                  Clarke, AL     5907     7455  2008
13                    Clay, AL     1722     4946  2008
14                Cleburne, AL     1166     5204  2008
15                  Coffee, AL     5068    14909  2008
16                 Colbert, AL     9698    14729  2008
17                 Conecuh, AL     3411     3461  2008
18                   Coosa, AL     2269     3245  2008
19               Covington, AL     3238    12431  2008
20                Crenshaw, AL     1938     4316  2008
21                 Cullman, AL     5855    28837  2008
22                    Dale, AL     5257    13873  2008
23                  Dallas, AL    13958     6791  2008
24                  DeKalb, AL     5654    17951  2008
25                  Elmore, AL     8268    25695  2008
26                Escambia, AL     5176     9365  2008
27                  Etowah, AL    13480    30562  2008
28                 Fayette, AL     1988     5875  2008
29                Franklin, AL     3469     8048  2008
30                  Geneva, AL     2106     9314  2008
31                  Greene, AL     4402      876  2008
32                    Hale, AL     4969     3196  2008
33                   Henry, AL     2990     5558  2008
34                 Houston, AL    12194    29205  2008
35                 Jackson, AL     6367    14068  2008
36               Jefferson, AL   166015   149843  2008
37                   Lamar, AL     1614     5419  2008
38              Lauderdale, AL    13318    24050  2008
39                Lawrence, AL     5159     9269  2008
40                     Lee, AL    21410    32344  2008
41               Limestone, AL     9530    23588  2008
42                 Lowndes, AL     5447     1807  2008
43                   Macon, AL     9444     1396  2008
44                 Madison, AL    64062    86910  2008
45                 Marengo, AL     5925     5511  2008
46                  Marion, AL     2597     9530  2008
47                Marshall, AL     7021    25680  2008
48                  Mobile, AL    81741    97670  2008
49                  Monroe, AL     5023     6173  2008
50              Montgomery, AL    61999    41972  2008
51                  Morgan, AL    13882    35986  2008
52                   Perry, AL     4423     1676  2008
53                 Pickens, AL     4584     5426  2008
54                    Pike, AL     5856     7981  2008
55                Randolph, AL     3062     7169  2008
56                 Russell, AL    10078     8700  2008
57                  Shelby, AL    20575    68945  2008
58               St. Clair, AL     6088    27630  2008
59                  Sumter, AL     5218     1723  2008
60               Talladega, AL    13769    20109  2008
61              Tallapoosa, AL     6052    13105  2008
62              Tuscaloosa, AL    32738    45351  2008
63                  Walker, AL     7418    20719  2008
64              Washington, AL     3032     5592  2008
65                  Wilcox, AL     4553     1849  2008
66                 Winston, AL     1756     8099  2008
67                  Apache, AZ    15141     8381  2008
68                 Cochise, AZ    17944    27590  2008
69                Coconino, AZ    27064    19449  2008
70                    Gila, AZ     7566    13425  2008
71                  Graham, AZ     3487     8375  2008
72       

## 2012 Election

In [99]:
count, dem_vote, rep_vote = data(2012, candidates_2012)

# check to make sure lists are the same length
print(len(count), len(dem_vote), len(rep_vote))

# loop over counties list to convert from list of lists or strings, to list of strings
counties = [item for sublist in count for item in sublist]

# due to faulty data entry in townhall.com Hawaii's county Kalawao needs to be removed
# as well as the entries corresponding to Kauai, entered as '-', which offset data
del counties[518] 
del rep_vote[518]
del dem_vote[518]

rep_vote.remove('-') 
dem_vote.remove('-')

# empty DataFrame
results_2012 = pd.DataFrame()

# add lists to empty Data Frame
results_2012['county'] = counties
results_2012['dem_vote'] = dem_vote
results_2012['rep_vote'] = rep_vote
results_2012['year'] = 2012

results_2012

3113 3114 3114


county dem_vote rep_vote  year
0                  Autauga, AL     6354    17366  2012
1                  Baldwin, AL    18329    65772  2012
2                  Barbour, AL     5873     5539  2012
3                     Bibb, AL     2200     6131  2012
4                   Blount, AL     2961    20741  2012
5                  Bullock, AL     4058     1250  2012
6                   Butler, AL     4367     5081  2012
7                  Calhoun, AL    15500    30272  2012
8                 Chambers, AL     6853     7596  2012
9                 Cherokee, AL     2126     7494  2012
10                 Chilton, AL     3391    13910  2012
11                 Choctaw, AL     3785     4150  2012
12                  Clarke, AL     6317     7463  2012
13                    Clay, AL     1770     4802  2012
14                Cleburne, AL      971     5269  2012
15                  Coffee, AL     4899    14638  2012
16                 Colbert, AL     9160    13931  2012
17                 Conecuh, AL     3551     3434  2012
18                   Coosa, AL     2188     3028  2012
19               Covington, AL     3155    12148  2012
20                Crenshaw, AL     2048     4326  2012
21                 Cullman, AL     4855    27930  2012
22                    Dale, AL     5283    13105  2012
23                  Dallas, AL    14599     6284  2012
24                  DeKalb, AL     5235    18316  2012
25                  Elmore, AL     8940    26223  2012
26                Escambia, AL     5476     9263  2012
27                  Etowah, AL    12792    29102  2012
28                 Fayette, AL     1803     6034  2012
29                Franklin, AL     3171     7567  2012
30                  Geneva, AL     2039     9173  2012
31                  Greene, AL     4514      799  2012
32                    Hale, AL     5401     3205  2012
33                   Henry, AL     3046     5605  2012
34                 Houston, AL    12348    29214  2012
35                 Jackson, AL     5817    14422  2012
36               Jefferson, AL   159658   141413  2012
37                   Lamar, AL     1643     5453  2012
38              Lauderdale, AL    12504    23902  2012
39                Lawrence, AL     5055     8855  2012
40                     Lee, AL    21274    32062  2012
41               Limestone, AL     9809    25263  2012
42                 Lowndes, AL     5747     1754  2012
43                   Macon, AL     9045     1322  2012
44                 Madison, AL    61802    90679  2012
45                 Marengo, AL     6154     5321  2012
46                  Marion, AL     2249     9696  2012
47                Marshall, AL     6271    25785  2012
48                  Mobile, AL    78417    94566  2012
49                  Monroe, AL     4897     5730  2012
50              Montgomery, AL    62993    38283  2012
51                  Morgan, AL    13401    35309  2012
52                   Perry, AL     4536     1504  2012
53                 Pickens, AL     4448     5119  2012
54                    Pike, AL     6009     7939  2012
55                Randolph, AL     3076     7219  2012
56                 Russell, AL    10495     8276  2012
57                  Shelby, AL    19944    71243  2012
58               St. Clair, AL     5790    29001  2012
59                  Sumter, AL     5420     1585  2012
60               Talladega, AL    13878    19217  2012
61              Tallapoosa, AL     6252    12303  2012
62              Tuscaloosa, AL    32003    45703  2012
63                  Walker, AL     6551    21633  2012
64              Washington, AL     2971     5749  2012
65                  Wilcox, AL     4867     1676  2012
66                 Winston, AL     1286     8310  2012
67                  Apache, AZ    17147     8250  2012
68                 Cochise, AZ    17377    28197  2012
69                Coconino, AZ    26772    19720  2012
70                    Gila, AZ     7293    12846  2012
71                  Graham, AZ     3609     8076  2012
72       

## 2016 Election

In [100]:
count, dem_vote, rep_vote = data(2016, candidates_2016)

# check to make sure lists are the same length
print(len(count), len(dem_vote), len(rep_vote))

# loop over counties list to convert from list of lists or strings, to list of strings
counties = [item for sublist in count for item in sublist]

# empty DataFrame
results_2016 = pd.DataFrame()

# add lists to empty Data Frame
results_2016['county'] = counties
results_2016['dem_vote'] = dem_vote
results_2016['rep_vote'] = rep_vote
results_2016['year'] = 2016

results_2016

3111 3111 3111


county dem_vote rep_vote  year
0                  Autauga, AL     5908    18110  2016
1                  Baldwin, AL    18409    72780  2016
2                  Barbour, AL     4848     5431  2016
3                     Bibb, AL     1874     6733  2016
4                   Blount, AL     2150    22808  2016
5                  Bullock, AL     3530     1139  2016
6                   Butler, AL     3716     4891  2016
7                  Calhoun, AL    13197    32803  2016
8                 Chambers, AL     5763     7803  2016
9                 Cherokee, AL     1524     8809  2016
10                 Chilton, AL     2909    15068  2016
11                 Choctaw, AL     3109     4102  2016
12                  Clarke, AL     5712     7109  2016
13                    Clay, AL     1234     5230  2016
14                Cleburne, AL      684     5738  2016
15                  Coffee, AL     4194    15825  2016
16                 Colbert, AL     7296    16718  2016
17                 Conecuh, AL     3069     3413  2016
18                   Coosa, AL     1780     3376  2016
19               Covington, AL     2379    13222  2016
20                Crenshaw, AL     1663     4511  2016
21                 Cullman, AL     3730    32734  2016
22                    Dale, AL     4408    13798  2016
23                  Dallas, AL    12826     5784  2016
24                  DeKalb, AL     3682    21779  2016
25                  Elmore, AL     8436    27619  2016
26                Escambia, AL     4698    10282  2016
27                  Etowah, AL    10350    32132  2016
28                 Fayette, AL     1358     6705  2016
29                Franklin, AL     2197     9466  2016
30                  Geneva, AL     1522     9967  2016
31                  Greene, AL     4006      838  2016
32                    Hale, AL     4772     3172  2016
33                   Henry, AL     2286     5623  2016
34                 Houston, AL    10547    30567  2016
35                 Jackson, AL     3663    16643  2016
36               Jefferson, AL   151581   130614  2016
37                   Lamar, AL     1035     5819  2016
38              Lauderdale, AL     9877    27735  2016
39                Lawrence, AL     3611    10732  2016
40                     Lee, AL    20987    34321  2016
41               Limestone, AL     9340    28824  2016
42                 Lowndes, AL     4882     1751  2016
43                   Macon, AL     7237     1394  2016
44                 Madison, AL    62435    89199  2016
45                 Marengo, AL     5607     5224  2016
46                  Marion, AL     1432    11273  2016
47                Marshall, AL     4913    29217  2016
48                  Mobile, AL    68429    91087  2016
49                  Monroe, AL     4310     5771  2016
50              Montgomery, AL    58669    33928  2016
51                  Morgan, AL    11216    37392  2016
52                   Perry, AL     3823     1403  2016
53                 Pickens, AL     3972     5454  2016
54                    Pike, AL     5039     7681  2016
55                Randolph, AL     2290     7697  2016
56                 Russell, AL     9577     9210  2016
57                  Shelby, AL    22927    72846  2016
58               St. Clair, AL     5550    31579  2016
59                  Sumter, AL     4739     1581  2016
60               Talladega, AL    12108    20596  2016
61              Tallapoosa, AL     5271    12967  2016
62              Tuscaloosa, AL    31746    47701  2016
63                  Walker, AL     4486    24208  2016
64              Washington, AL     2366     6031  2016
65                  Wilcox, AL     4329     1737  2016
66                 Winston, AL      871     9225  2016
67                  Apache, AZ    12196     5315  2016
68                 Cochise, AZ    15291    25036  2016
69                Coconino, AZ    25308    16573  2016
70                    Gila, AZ     6746    13672  2016
71                  Graham, AZ     3301     8025  2016
72       

In [101]:
results_2004.shape, results_2008.shape, results_2012.shape, results_2016.shape

((3110, 4), (3112, 4), (3112, 4), (3111, 4))

In [102]:
results_2016

county dem_vote rep_vote  year
0                  Autauga, AL     5908    18110  2016
1                  Baldwin, AL    18409    72780  2016
2                  Barbour, AL     4848     5431  2016
3                     Bibb, AL     1874     6733  2016
4                   Blount, AL     2150    22808  2016
5                  Bullock, AL     3530     1139  2016
6                   Butler, AL     3716     4891  2016
7                  Calhoun, AL    13197    32803  2016
8                 Chambers, AL     5763     7803  2016
9                 Cherokee, AL     1524     8809  2016
10                 Chilton, AL     2909    15068  2016
11                 Choctaw, AL     3109     4102  2016
12                  Clarke, AL     5712     7109  2016
13                    Clay, AL     1234     5230  2016
14                Cleburne, AL      684     5738  2016
15                  Coffee, AL     4194    15825  2016
16                 Colbert, AL     7296    16718  2016
17                 Conecuh, AL     3069     3413  2016
18                   Coosa, AL     1780     3376  2016
19               Covington, AL     2379    13222  2016
20                Crenshaw, AL     1663     4511  2016
21                 Cullman, AL     3730    32734  2016
22                    Dale, AL     4408    13798  2016
23                  Dallas, AL    12826     5784  2016
24                  DeKalb, AL     3682    21779  2016
25                  Elmore, AL     8436    27619  2016
26                Escambia, AL     4698    10282  2016
27                  Etowah, AL    10350    32132  2016
28                 Fayette, AL     1358     6705  2016
29                Franklin, AL     2197     9466  2016
30                  Geneva, AL     1522     9967  2016
31                  Greene, AL     4006      838  2016
32                    Hale, AL     4772     3172  2016
33                   Henry, AL     2286     5623  2016
34                 Houston, AL    10547    30567  2016
35                 Jackson, AL     3663    16643  2016
36               Jefferson, AL   151581   130614  2016
37                   Lamar, AL     1035     5819  2016
38              Lauderdale, AL     9877    27735  2016
39                Lawrence, AL     3611    10732  2016
40                     Lee, AL    20987    34321  2016
41               Limestone, AL     9340    28824  2016
42                 Lowndes, AL     4882     1751  2016
43                   Macon, AL     7237     1394  2016
44                 Madison, AL    62435    89199  2016
45                 Marengo, AL     5607     5224  2016
46                  Marion, AL     1432    11273  2016
47                Marshall, AL     4913    29217  2016
48                  Mobile, AL    68429    91087  2016
49                  Monroe, AL     4310     5771  2016
50              Montgomery, AL    58669    33928  2016
51                  Morgan, AL    11216    37392  2016
52                   Perry, AL     3823     1403  2016
53                 Pickens, AL     3972     5454  2016
54                    Pike, AL     5039     7681  2016
55                Randolph, AL     2290     7697  2016
56                 Russell, AL     9577     9210  2016
57                  Shelby, AL    22927    72846  2016
58               St. Clair, AL     5550    31579  2016
59                  Sumter, AL     4739     1581  2016
60               Talladega, AL    12108    20596  2016
61              Tallapoosa, AL     5271    12967  2016
62              Tuscaloosa, AL    31746    47701  2016
63                  Walker, AL     4486    24208  2016
64              Washington, AL     2366     6031  2016
65                  Wilcox, AL     4329     1737  2016
66                 Winston, AL      871     9225  2016
67                  Apache, AZ    12196     5315  2016
68                 Cochise, AZ    15291    25036  2016
69                Coconino, AZ    25308    16573  2016
70                    Gila, AZ     6746    13672  2016
71                  Graham, AZ     3301     8025  2016
72       

In [103]:
for x in results_2004.county:
    if 'Co.' in x:
        print(x)

St. Louis Co., MO
Bedford Co., VA
Fairfax Co., VA
Franklin Co., VA
Richmond Co., VA
Roanoke Co., VA


In [111]:
results_2004[results_2004.county == 'Richmond Co., VA']

county dem_vote rep_vote  year
2893  Richmond Co., VA     1243     2082  2004

In [116]:
results_2004.loc[2892, 'county'] = 'Richmond Co., VA'
results_2004.loc[2893, 'county'] = 'Richmond, VA'
results_2008.loc[2894, 'county'] = 'Richmond Co., VA'
results_2008.loc[2895, 'county'] = 'Richmond, VA'
results_2012.loc[2894, 'county'] = 'Richmond Co., VA'
results_2012.loc[2895, 'county'] = 'Richmond, VA'
results_2016.loc[2893, 'county'] = 'Richmond Co., VA'
results_2016.loc[2894, 'county'] = 'Richmond, VA'


results_2004.loc[1553, 'county'] = 'St. Louis Co., MO'
results_2004.loc[1554, 'county'] = 'St. Louis, MO'
results_2008.loc[1553, 'county'] = 'St. Louis Co., MO'
results_2008.loc[1554, 'county'] = 'St. Louis, MO'
results_2012.loc[1553, 'county'] = 'St. Louis Co., MO'
results_2012.loc[1554, 'county'] = 'St. Louis, MO'
results_2016.loc[1553, 'county'] = 'St. Louis Co., MO'
results_2016.loc[1554, 'county'] = 'St. Louis, MO'


results_2004.loc[2797, 'county'] = 'Bedford Co., VA'
results_2004.loc[2798, 'county'] = 'Bedford, VA'
results_2008.loc[2799, 'county'] = 'Bedford Co., VA'
results_2008.loc[2800, 'county'] = 'Bedford, VA'
results_2012.loc[2799, 'county'] = 'Bedford Co., VA'
results_2012.loc[2800, 'county'] = 'Bedford, VA'
results_2016.loc[2799, 'county'] = 'Bedford, VA'


results_2004.loc[2825, 'county'] = 'Fairfax Co., VA'
results_2004.loc[2826, 'county'] = 'Fairfax, VA'
results_2008.loc[2827, 'county'] = 'Fairfax Co., VA'
results_2008.loc[2828, 'county'] = 'Fairfax, VA'
results_2012.loc[2827, 'county'] = 'Fairfax Co., VA'
results_2012.loc[2828, 'county'] = 'Fairfax, VA'
results_2016.loc[2826, 'county'] = 'Fairfax Co., VA'
results_2016.loc[2827, 'county'] = 'Fairfax, VA'


results_2004.loc[2894, 'county'] = 'Roanoke Co., VA'
results_2004.loc[2895, 'county'] = 'Roanoke, VA'
results_2008.loc[2896, 'county'] = 'Roanoke Co., VA'
results_2008.loc[2896, 'county'] = 'Roanoke, VA'
results_2012.loc[2896, 'county'] = 'Roanoke Co., VA'
results_2012.loc[2897, 'county'] = 'Roanoke, VA'
results_2016.loc[2895, 'county'] = 'Roanoke Co., VA'
results_2016.loc[2896, 'county'] = 'Roanoke, VA'


results_2004.loc[2831, 'county'] = 'Franklin Co., VA'
results_2004.loc[2832, 'county'] = 'Franklin, VA'
results_2008.loc[2833, 'county'] = 'Franklin Co., VA'
results_2008.loc[2834, 'county'] = 'Franklin, VA'
results_2012.loc[2833, 'county'] = 'Franklin Co., VA'
results_2012.loc[2834, 'county'] = 'Franklin, VA'
results_2016.loc[2832, 'county'] = 'Franklin Co., VA'
results_2016.loc[2833, 'county'] = 'Franklin, VA'

In [117]:
len(results_2004.county.unique()), results_2004.shape

(3110, (3110, 4))

In [118]:
len(results_2008.county.unique()), results_2008.shape

(3112, (3112, 4))

In [119]:
len(results_2012.county.unique()), results_2012.shape

(3112, (3112, 4))

In [120]:
len(results_2016.county.unique()), results_2016.shape

(3111, (3111, 4))

In [121]:
# puts dataframe in to .csv files in same folder as notebook

results_2004.to_csv('./csv_files/results_2004', index=False)

results_2008.to_csv('./csv_files/results_2008', index=False)

results_2012.to_csv('./csv_files/results_2012', index=False)

results_2016.to_csv('./csv_files/results_2016', index=False)

Note: inspiration for this webscrape came from existing code by tonmcg repository County_Level_Election_Results_12-16. This code only worked for the 2012 and 2016 elections. It also returned a dataframe that wasn't useful to me. So I wrote my own code, as shwon above.
https://github.com/tonmcg/County_Level_Election_Results_12-16